In [ ]:
# import os
# import json

# input_json_dir = '/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/val/labels'
# output_yolo_dir = '/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/val/labels'

# os.makedirs(output_yolo_dir, exist_ok=True)

# for file in os.listdir(input_json_dir):
#     if not file.endswith(".json"):
#         continue

#     with open(os.path.join(input_json_dir, file), 'r') as f:
#         data = json.load(f)

#     bbox = data["bbox"]  # [x_min, y_min, x_max, y_max]
#     cls = data["class"]
    

#     # Convert (x_min, y_min, x_max, y_max) => YOLO (x_center, y_center, width, height)
#     x_min, y_min, x_max, y_max = bbox
#     x_center = (x_min + x_max) / 2
#     y_center = (y_min + y_max) / 2
#     width = abs(x_max - x_min)
#     height = abs(y_max - y_min)

#     yolo_format = f"{cls} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}"

#     # Save as .txt with same filename
#     out_path = os.path.join(output_yolo_dir, file.replace(".json", ".txt"))
#     with open(out_path, "w") as out_file:
#         out_file.write(yolo_format + "\n")

# print("✅ YOLO label conversion complete.")


In [ ]:
import torch
import numpy as np
from pathlib import Path
import shutil
from yolov5.models.yolo import Model
from yolov5.utils.dataloaders import create_dataloader, LoadImages
from yolov5.utils.torch_utils import select_device
from yolov5.utils.loss import ComputeLoss
import yaml
import os
from yolov5.utils.general import non_max_suppression, scale_boxes
from tqdm import tqdm  # Import tqdm for progress bar

# Choose device (GPU or CPU) with fallback to CPU
device = select_device('cuda:0' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# Load hyperparameters from hyp.scratch-med.yaml
with open('/kaggle/working/yolov5/data/hyps/hyp.scratch-med.yaml', 'r') as f:  # Adjusted path for Kaggle
    hyp = yaml.safe_load(f)

# Create or load Model (YOLOv5) with 1 class (e.g., text regions)
model = Model(cfg='/kaggle/working/yolov5/models/yolov5s.yaml', ch=3, nc=1).to(device)
model.hyp = hyp  # Manually attach hyperparameters to the model

# Image size and original dimensions
imgsz = 640  # Target image size
orig_width, orig_height = 2552, 3302  # Original image dimensions

# Function to adjust coordinates
def adjust_labels(label_dir, orig_w, orig_h, target_sz):
    for label_file in os.listdir(label_dir):
        if label_file.endswith('.txt'):
            file_path = os.path.join(label_dir, label_file)
            with open(file_path, 'r') as f:
                lines = f.readlines()
            with open(file_path, 'w') as f:  # Safe to write since it's in /kaggle/working/
                for line in lines:
                    data = line.strip().split()
                    class_id = int(data[0])
                    coords = np.array(list(map(float, data[1:])))
                    # Rescale to target_sz
                    new_coords = coords * [target_sz / orig_w, target_sz / orig_h, target_sz / orig_w, target_sz / orig_h]
                    new_line = f"{class_id} {' '.join(map(str, new_coords))}\n"
                    f.write(new_line)

# Create working directory structure and copy dataset
working_data_dir = Path('/kaggle/working/aug_data')
working_data_dir.mkdir(parents=True, exist_ok=True)

# Copy train and val images
shutil.copytree('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/train/images', 
                '/kaggle/working/aug_data/train/images', dirs_exist_ok=True)
shutil.copytree('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/val/images', 
                '/kaggle/working/aug_data/val/images', dirs_exist_ok=True)

# Copy and adjust train labels
train_label_src = Path('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/train/labels_yolo')
train_label_dest = Path('/kaggle/working/aug_data/train/labels_yolo')
train_label_dest.mkdir(parents=True, exist_ok=True)
for item in train_label_src.glob('*'):
    if item.is_file():
        shutil.copy2(item, train_label_dest / item.name)
adjust_labels(train_label_dest, orig_width, orig_height, imgsz)

# Copy and adjust val labels
val_label_src = Path('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/val/labels_yolo')
val_label_dest = Path('/kaggle/working/aug_data/val/labels_yolo')
val_label_dest.mkdir(parents=True, exist_ok=True)
for item in val_label_src.glob('*'):
    if item.is_file():
        shutil.copy2(item, val_label_dest / item.name)
adjust_labels(val_label_dest, orig_width, orig_height, imgsz)

# Load the dataset from the working directory
train_dataset = create_dataloader(
    Path('/kaggle/working/aug_data/train/images'),
    imgsz=imgsz,
    batch_size=16,
    stride=32,
    rect=False,
    workers=1,
    pad=0.5
)[0]
val_dataset = create_dataloader(
    Path('/kaggle/working/aug_data/val/images'),
    imgsz=imgsz,
    batch_size=16,
    stride=32,
    rect=False,
    workers=1,
    pad=0.5
)[0]

# Set up loss
compute_loss = ComputeLoss(model, autobalance=False)

# Set up optimizer and learning rate scheduler
optimizer = torch.optim.SGD(model.parameters(), lr=0.01, momentum=0.937, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=50)

# Set number of epochs
epochs = 50

# Training loop with tqdm
for epoch in tqdm(range(epochs), desc="Epochs"):
    model.train()
    total_loss = 0.0
    num_batches = len(train_dataset)
    
    # Batch loop with tqdm
    for batch_idx, (images, targets, paths, _) in tqdm(enumerate(train_dataset), total=num_batches, desc="Batches", leave=False):
        images = images.to(device).float() / 255.0  # Explicitly normalize to [0, 1] and convert to float32
        targets = targets.to(device)
        
        # Forward pass
        pred = model(images)
        loss, loss_items = compute_loss(pred, targets)
        
        # Backward pass
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        
        total_loss += loss.item()
    
    avg_loss = total_loss / num_batches
    scheduler.step()
    print(f'Epoch {epoch+1}/{epochs}, Average Loss: {avg_loss:.4f}')

print("Training completed!")


In [1]:
import torch
import numpy as np
from pathlib import Path
import shutil
from yolov5.models.yolo import Model
from yolov5.utils.dataloaders import create_dataloader, LoadImages
from yolov5.utils.torch_utils import select_device
from yolov5.utils.loss import ComputeLoss
import yaml
import os
from yolov5.utils.general import non_max_suppression, scale_boxes
from tqdm import tqdm  # Import tqdm for progress bar

torch.cuda.empty_cache()

In [3]:
import torch
import numpy as np
from pathlib import Path
import shutil
from yolov5.models.yolo import Model
from yolov5.utils.dataloaders import create_dataloader, LoadImages
from yolov5.utils.torch_utils import select_device
from yolov5.utils.loss import ComputeLoss
import yaml
import os
from yolov5.utils.general import non_max_suppression, scale_boxes
from tqdm import tqdm  # Import tqdm for progress bar

# Clone the latest YOLOv5 repository
!git clone https://github.com/ultralytics/yolov5.git
%cd yolov5
!pip install -r requirements.txt
%cd ..

# Choose device (GPU or CPU) with fallback to CPU
device = select_device('cuda:0' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# Load hyperparameters from hyp.scratch-med.yaml
with open('/kaggle/working/yolov5/data/hyps/hyp.scratch-med.yaml', 'r') as f:
    hyp = yaml.safe_load(f)

# Create or load Model (YOLOv5) with 1 class (e.g., text regions)
model = Model(cfg='/kaggle/working/yolov5/models/yolov5s.yaml', ch=3, nc=1).to(device)
model.hyp = hyp  # Manually attach hyperparameters to the model

# Enable mixed precision training
model.half()  # Convert model to FP16
torch.cuda.amp.autocast(enabled=True)  # Enable autocast for mixed precision

# Use adjusted image size that is a multiple of stride (32)
imgsz = 2560  # Adjusted width to nearest multiple of 32
orig_width, orig_height = 2552, 3302  # Original image dimensions
target_height = 3328  # Adjusted height to nearest multiple of 32

# Function to adjust coordinates to new target size
def adjust_labels(label_dir, orig_w, orig_h, target_w, target_h):
    for label_file in os.listdir(label_dir):
        if label_file.endswith('.txt'):
            file_path = os.path.join(label_dir, label_file)
            with open(file_path, 'r') as f:
                lines = f.readlines()
            with open(file_path, 'w') as f:
                for line in lines:
                    data = line.strip().split()
                    class_id = int(data[0])
                    coords = np.array(list(map(float, data[1:])))
                    # Rescale normalized coordinates to new target size
                    new_coords = coords * [target_w / orig_w, target_h / orig_h, target_w / orig_w, target_h / orig_h]
                    new_line = f"{class_id} {' '.join(map(str, new_coords))}\n"
                    f.write(new_line)

# Create working directory structure and copy dataset
working_data_dir = Path('/kaggle/working/aug_data')
working_data_dir.mkdir(parents=True, exist_ok=True)

# Copy train, val, and test images
shutil.copytree('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/train/images', 
                '/kaggle/working/aug_data/train/images', dirs_exist_ok=True)
shutil.copytree('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/val/images', 
                '/kaggle/working/aug_data/val/images', dirs_exist_ok=True)
shutil.copytree('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/test/images', 
                '/kaggle/working/aug_data/test/images', dirs_exist_ok=True)

# Copy and adjust train labels
train_label_src = Path('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/train/labels_yolo')
train_label_dest = Path('/kaggle/working/aug_data/train/labels_yolo')
train_label_dest.mkdir(parents=True, exist_ok=True)
for item in train_label_src.glob('*'):
    if item.is_file():
        shutil.copy2(item, train_label_dest / item.name)
adjust_labels(train_label_dest, orig_width, orig_height, imgsz, target_height)

# Copy and adjust val labels
val_label_src = Path('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/val/labels_yolo')
val_label_dest = Path('/kaggle/working/aug_data/val/labels_yolo')
val_label_dest.mkdir(parents=True, exist_ok=True)
for item in val_label_src.glob('*'):
    if item.is_file():
        shutil.copy2(item, val_label_dest / item.name)
adjust_labels(val_label_dest, orig_width, orig_height, imgsz, target_height)

# Copy and adjust test labels
test_label_src = Path('/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/test/labels_yolo')
test_label_dest = Path('/kaggle/working/aug_data/test/labels_yolo')
test_label_dest.mkdir(parents=True, exist_ok=True)
for item in test_label_src.glob('*'):
    if item.is_file():
        shutil.copy2(item, test_label_dest / item.name)
adjust_labels(test_label_dest, orig_width, orig_height, imgsz, target_height)

# Load the dataset from the working directory with adjusted size
train_dataset = create_dataloader(
    Path('/kaggle/working/aug_data/train/images'),
    imgsz=imgsz,  # Use adjusted width
    batch_size=1,  # Process one image at a time to avoid mismatches
    stride=32,
    rect=False,
    workers=1,
    pad=0.5,
    augment=False  # Disable augmentations to preserve original size
)[0]
val_dataset = create_dataloader(
    Path('/kaggle/working/aug_data/val/images'),
    imgsz=imgsz,  # Use adjusted width
    batch_size=1,  # Process one image at a time to avoid mismatches
    stride=32,
    rect=False,
    workers=1,
    pad=0.5,
    augment=False  # Disable augmentations to preserve original size
)[0]
test_dataset = create_dataloader(
    Path('/kaggle/working/aug_data/test/images'),
    imgsz=imgsz,  # Use adjusted width
    batch_size=1,  # Process one image at a time to avoid mismatches
    stride=32,
    rect=False,
    workers=1,
    pad=0.5,
    augment=False  # Disable augmentations to preserve original size
)[0]

# Set up loss
compute_loss = ComputeLoss(model, autobalance=False)

# Set up optimizer and learning rate scheduler
optimizer = torch.optim.SGD(model.parameters(), lr=0.01, momentum=0.937, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=50)

# Set number of epochs
epochs = 50

# Training loop with tqdm and mixed precision
for epoch in tqdm(range(epochs), desc="Epochs"):
    model.train()
    total_loss = 0.0
    num_batches = len(train_dataset)
    
    # Batch loop with tqdm
    for batch_idx, (images, targets, paths, _) in tqdm(enumerate(train_dataset), total=num_batches, desc="Batches", leave=False):
        print(f"Image shape: {images.shape}")  # Debug: Check image dimensions
        images = images.to(device).half()  # Convert images to FP16
        targets = targets.to(device)
        
        # Forward pass with autocast
        with torch.cuda.amp.autocast():
            pred = model(images)
            loss, loss_items = compute_loss(pred, targets)
        
        # Backward pass
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        
        total_loss += loss.item()
    
    avg_loss = total_loss / num_batches
    scheduler.step()
    print(f'Epoch {epoch+1}/{epochs}, Average Loss: {avg_loss:.4f}')

print("Training completed!")



fatal: destination path 'yolov5' already exists and is not an empty directory.
/kaggle/working/yolov5


YOLOv5 🚀 v7.0-411-gf4d8a84c Python-3.11.11 torch-2.5.1+cu124 CUDA:0 (Tesla P100-PCIE-16GB, 16269MiB)



/kaggle/working
Using device: cuda:0


Overriding model.yaml nc=80 with nc=1

                 from  n    params  module                                  arguments                     
  0                -1  1      3520  models.common.Conv                      [3, 32, 6, 2, 2]              
  1                -1  1     18560  models.common.Conv                      [32, 64, 3, 2]                
  2                -1  1     18816  models.common.C3                        [64, 64, 1]                   
  3                -1  1     73984  models.common.Conv                      [64, 128, 3, 2]               
  4                -1  2    115712  models.common.C3                        [128, 128, 2]                 
  5                -1  1    295424  models.common.Conv                      [128, 256, 3, 2]              
  6                -1  3    625152  models.common.C3                        [256, 256, 3]                 
  7                -1  1   1180672  models.common.Conv                      [256, 512, 3, 2]             

Image shape: torch.Size([1, 3, 2560, 2560])


...

Image shape: torch.Size([1, 3, 2560, 2560])



Batches: 100%|█████████▉| 299/300 [02:39<00:00,  1.88it/s]/tmp/ipykernel_211/2235698274.py:152: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast():


Image shape: torch.Size([1, 3, 2560, 2560])



Epochs: 100%|██████████| 50/50 [2:12:58<00:00, 159.57s/it]

Epoch 50/50, Average Loss: 0.0068
Training completed!


In [4]:
# Save the model
save_dir = Path('/kaggle/working/')
save_dir.mkdir(parents=True, exist_ok=True)
torch.save(model.state_dict(), save_dir / 'best.pt')

import cv2
import matplotlib.pyplot as plt

# Inference on a test image with bounding box saving and display
def infer_image(model, test_image_path, imgsz=640, conf_thres=0.25, iou_thres=0.45, output_dir='/kaggle/working/output'):
    model.eval()
    dataset = LoadImages(test_image_path, img_size=imgsz, stride=32, auto=True)
    
    # Create output directory if it doesn't exist
    output_dir = Path(output_dir)
    output_dir.mkdir(parents=True, exist_ok=True)
    
    for path, img, im0s, vid_cap, s in dataset:  # Unpack 5 values
        img = torch.from_numpy(img).to(device).float() / 255.0  # Normalize to [0, 1] and convert to float32
        img = img[None]  # Add batch dimension
        
        # Inference
        with torch.no_grad():
            pred = model(img, augment=False)[0]
            pred = non_max_suppression(pred, conf_thres, iou_thres)
        
        # Draw bounding boxes on the original image
        annotated_image = im0s.copy()  # Create a copy to annotate
        coords_list = []  # List to store coordinates
        if len(pred[0]):
            print("Register number detected!")
            for *xyxy, conf, cls in pred[0]:
                # Convert xyxy to integer coordinates
                x1, y1, x2, y2 = map(int, xyxy)
                coords = (x1, y1, x2, y2, conf.item())  # Store coordinates and confidence
                coords_list.append(coords)
                # Draw rectangle
                cv2.rectangle(annotated_image, (x1, y1), (x2, y2), (0, 255, 0), 2)  # Green box with thickness 2
                # Add confidence text
                label = f"{conf:.2f}"
                cv2.putText(annotated_image, label, (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)
        
            # Convert BGR (OpenCV) to RGB for matplotlib
            annotated_image_rgb = cv2.cvtColor(annotated_image, cv2.COLOR_BGR2RGB)
            
            # Display the image
            plt.figure(figsize=(10, 10))
            plt.imshow(annotated_image_rgb)
            plt.title("Detected Register Number with Bounding Boxes")
            plt.axis('off')
            plt.show()
            
            # Save the annotated image
            output_path = output_dir / f"output_{Path(path).stem}.jpg"
            cv2.imwrite(str(output_path), annotated_image)
            print(f"Saved annotated image to {output_path}")
            
            # Print coordinates
            for i, (x1, y1, x2, y2, conf) in enumerate(coords_list):
                print(f"Bounding Box {i+1}: (x1: {x1}, y1: {y1}, x2: {x2}, y2: {y2}, confidence: {conf:.4f})")
        else:
            print("No register number detected in the image.")
    
    # Return None if no visualization is needed
    return None

# Run inference on test image and save/display output
test_image_path = '/kaggle/input/register-number-images-and-their-yolo-labels/aug_data/test/images/00001_212221040002_19CS414_CIA2.1.jpg'
result = infer_image(model, test_image_path, imgsz=imgsz)
print("Inference completed! Bounding box coordinates are printed above and images are saved if detections were made.")


RuntimeError: Input type (torch.cuda.FloatTensor) and weight type (torch.cuda.HalfTensor) should be the same

In [6]:
# Save the model
save_dir = Path('/kaggle/working/runs/train/exp/weights')
save_dir.mkdir(parents=True, exist_ok=True)
torch.save(model.state_dict(), save_dir / 'best.pt')

# Basic inference on test dataset
def infer_test(model, test_dataset, imgsz=(2560, 3328), conf_thres=0.25, iou_thres=0.45):
    model.eval()
    for batch_idx, (images, targets, paths, _) in tqdm(enumerate(test_dataset), desc="Testing", total=len(test_dataset)):
        print(f"Input shape before model: {images.shape}")  # Debug: Check input shape
        images = images.to(device).half()  # Convert images to FP16
        # Remove the extra [None] since the dataset is already batched
        with torch.no_grad():
            with torch.amp.autocast('cuda'):  # Updated to recommended syntax
                pred = model(images)
                pred = non_max_suppression(pred, conf_thres, iou_thres)
        
        # Process predictions (optional: print or save results)
        for i, det in enumerate(pred):
            if len(det):
                print(f"Image {paths[i]} has detections:")
                for *xyxy, conf, cls in det:
                    x1, y1, x2, y2 = map(int, xyxy)
                    print(f"Bounding Box: (x1: {x1}, y1: {y1}, x2: {x2}, y2: {y2}, confidence: {conf:.4f})")

# Run inference on test dataset
print("Running inference on test dataset...")
infer_test(model, test_dataset, imgsz=(2560, 3328))
print("Inference completed!")

Running inference on test dataset...


Testing:   0%|          | 0/120 [00:00<?, ?it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])


Testing:   2%|▏         | 2/120 [00:00<00:28,  4.17it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])


...

Input shape before model: torch.Size([1, 3, 2560, 2560])


Testing:  98%|█████████▊| 118/120 [00:25<00:00,  4.67it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])
Input shape before model: torch.Size([1, 3, 2560, 2560])


Testing: 100%|██████████| 120/120 [00:25<00:00,  4.70it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])
Inference completed!


In [7]:
# Create directory for saving annotated images
output_dir = Path('/kaggle/working/annotated_test_images')
output_dir.mkdir(parents=True, exist_ok=True)

# Basic inference on test dataset with image saving
def infer_test(model, test_dataset, imgsz=(2560, 3328), conf_thres=0.25, iou_thres=0.45):
    model.eval()
    for batch_idx, (images, targets, paths, shapes) in tqdm(enumerate(test_dataset), desc="Testing", total=len(test_dataset)):
        print(f"Input shape before model: {images.shape}")  # Debug: Check input shape
        images = images.to(device).half()  # Convert images to FP16
        
        with torch.no_grad():
            with torch.amp.autocast('cuda'):  # Updated to recommended syntax
                pred = model(images)  # Shape: [batch_size, num_anchors, num_classes + 5]
                pred = non_max_suppression(pred, conf_thres, iou_thres)
        
        # Process predictions and save images with bounding boxes
        for i, det in enumerate(pred):
            if len(det):
                # Load the original image for drawing
                img_path = paths[i]
                img = cv2.imread(img_path)
                if img is None:
                    print(f"Failed to load image: {img_path}")
                    continue
                
                # Convert BGR (OpenCV) to RGB
                img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
                
                # Scale bounding boxes to original image size
                det[:, :4] = scale_boxes(imgsz, det[:, :4], shapes[i][0]).round().int()
                
                # Draw bounding boxes
                for *xyxy, conf, cls in det:
                    x1, y1, x2, y2 = map(int, xyxy)
                    # Draw rectangle
                    cv2.rectangle(img, (x1, y1), (x2, y2), (0, 255, 0), 2)
                    # Add confidence text
                    label = f"{conf:.2f}"
                    cv2.putText(img, label, (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)
                
                # Convert back to BGR for saving
                img = cv2.cvtColor(img, cv2.COLOR_RGB2BGR)
                
                # Save the annotated image
                filename = Path(img_path).name
                output_path = output_dir / f"annotated_{filename}"
                cv2.imwrite(str(output_path), img)
                print(f"Saved annotated image: {output_path}")
            else:
                print(f"No detections for image: {paths[i]}")

# Run inference on test dataset
print("Running inference on test dataset...")
infer_test(model, test_dataset, imgsz=(2560, 3328))
print("Inference completed!")

Running inference on test dataset...


Testing:   0%|          | 0/120 [00:00<?, ?it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])


Testing:   1%|          | 1/120 [00:00<00:25,  4.73it/s]

No detections for image: /kaggle/working/aug_data/test/images/00001_212221040002_19CS414_CIA2.1.jpg
Input shape before model: torch.Size([1, 3, 2560, 2560])


...

No detections for image: /kaggle/working/aug_data/test/images/00001_212221040027_19EE305_CIA3.8.jpg
Input shape before model: torch.Size([1, 3, 2560, 2560])


Testing:  99%|█████████▉| 119/120 [00:25<00:00,  4.68it/s]

No detections for image: /kaggle/working/aug_data/test/images/00001_212221040027_19EE305_CIA3.9.jpg
Input shape before model: torch.Size([1, 3, 2560, 2560])


Testing: 100%|██████████| 120/120 [00:25<00:00,  4.67it/s]

No detections for image: /kaggle/working/aug_data/test/images/00001_212221040002_19CS414_CIA2.0.jpg
Inference completed!


In [9]:
def infer_test(model, test_dataset, imgsz=(2560, 3328), conf_thres=0.25, iou_thres=0.45):
    model.eval()
    for batch_idx, (images, targets, paths, shapes) in tqdm(enumerate(test_dataset), desc="Testing", total=len(test_dataset)):
        print(f"Input shape before model: {images.shape}")
        images = images.to(device).half()
        
        with torch.no_grad():
            with torch.amp.autocast('cuda'):
                pred = model(images)
                pred = non_max_suppression(pred, conf_thres, iou_thres)
        
        # Load and save image (with or without detections)
        img_path = paths[0]
        img = cv2.imread(img_path)
        if img is None:
            print(f"Failed to load image: {img_path}")
            continue
        img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        
        if len(pred[0]):
            det = pred[0]
            det[:, :4] = scale_boxes(imgsz, det[:, :4], shapes[0][0]).round().int()
            for *xyxy, conf, cls in det:
                x1, y1, x2, y2 = map(int, xyxy)
                cv2.rectangle(img, (x1, y1), (x2, y2), (0, 255, 0), 2)
                label = f"{conf:.2f}"
                cv2.putText(img, label, (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)
        
        img = cv2.cvtColor(img, cv2.COLOR_RGB2BGR)
        filename = Path(img_path).name
        output_path = output_dir / f"annotated_{filename}"
        cv2.imwrite(str(output_path), img)
        print(f"Saved annotated image: {output_path}" if len(pred[0]) else f"No detections, saved: {output_path}")

In [10]:
infer_test(model, test_dataset, imgsz=(2560, 3328), conf_thres=0.1, iou_thres=0.45)

Testing:   1%|          | 1/120 [00:00<00:40,  2.93it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])
No detections, saved: /kaggle/working/annotated_test_images/annotated_00001_212221040002_19CS414_CIA2.1.jpg


Testing:   2%|▏         | 2/120 [00:00<00:37,  3.12it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])
No detections, saved: /kaggle/working/annotated_test_images/annotated_00001_212221040002_19CS414_CIA2.10.jpg


Testing:   2%|▎         | 3/120 [00:00<00:35,  3.25it/s]

...

Input shape before model: torch.Size([1, 3, 2560, 2560])
No detections, saved: /kaggle/working/annotated_test_images/annotated_00001_212221040027_19EE305_CIA3.8.jpg


Testing:  99%|█████████▉| 119/120 [00:38<00:00,  2.98it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])
No detections, saved: /kaggle/working/annotated_test_images/annotated_00001_212221040027_19EE305_CIA3.9.jpg


Testing: 100%|██████████| 120/120 [00:38<00:00,  3.12it/s]

Input shape before model: torch.Size([1, 3, 2560, 2560])
No detections, saved: /kaggle/working/annotated_test_images/annotated_00001_212221040002_19CS414_CIA2.0.jpg
